In [ ]:
from datetime import datetime
import sqlite3

import plotly.graph_objects as go
import pandas as pd

In [ ]:
sqlite_file = input("Sqlite file: ")
conn = sqlite3.connect(sqlite_file)

In [ ]:
query = '''
SELECT timestamp, filament_variant_id, available, region
    FROM availability
    LEFT JOIN measurements ON availability.measurement_id = measurements.id
    LEFT JOIN filament_variants ON availability.filament_variant_id = filament_variants.id
    LEFT JOIN filaments ON filament_variants.filament_id = filaments.id
'''
df = pd.read_sql(query, conn)

all_timestamps = list(df['timestamp'].unique())
all_regions = list(df['region'].unique())
# idk why there is a None in the dataset. when I manually review it there is no None region
all_regions.remove(None)

available = {region: [] for region in all_regions}
not_available = {region: [] for region in all_regions}

for timestamp in all_timestamps:
    values = df.query(f'timestamp <= {timestamp}').drop(columns=['timestamp']).drop_duplicates(keep='last', subset=['filament_variant_id', 'region'])
    
    for region in all_regions:
        available[region].append(len(values.query(f'(available == 1) and (region == "{region}")')))
        not_available[region].append(len(values.query(f'(available == 0) and (region == "{region}")')))

fig = go.Figure()
for region in all_regions:
    timestamp_datetime = [datetime.fromtimestamp(timestamp) for timestamp in all_timestamps]
    fig.add_trace(go.Scatter(x=timestamp_datetime, y=available[region], mode='markers+lines', name=f'Available ({region.upper()})'))
    fig.add_trace(go.Scatter(x=timestamp_datetime, y=not_available[region], mode='markers+lines', name=f'Not available ({region.upper()})'))
fig.update_layout(title='Total availability', xaxis_title='Time', yaxis_title='Availability', hovermode='x unified')
fig.show()

fig = go.Figure()
for region in all_regions:
    timestamp_datetime = [datetime.fromtimestamp(timestamp) for timestamp in all_timestamps]
    ratios = []
    ratio_texts = []
    for i in range(len(available[region])):
        ratios.append(round((available[region][i] / (available[region][i] + not_available[region][i])) * 100, 2))
        ratio_texts.append(f'({available[region][i]} / {available[region][i] + not_available[region][i]})')
        
    fig.add_trace(go.Scatter(x=timestamp_datetime, y=ratios, text=ratio_texts, mode='markers+lines', name=region.upper()))
fig.update_layout(title='Availability Ratio', xaxis_title='Time', yaxis_title='Availability in %', yaxis_range=[0, 100], yaxis_ticksuffix = '%', hovermode='x unified')
fig.show()